        1_6_230104_016_bus_display
         
         4-7 section
         
         data : 

In [1]:
#1. package load
import requests
import json
import os
import math
import time
import numpy as np
import pandas as pd
import geopandas as gpd
import folium
import matplotlib.pyplot as plt

from shapely.geometry import mapping, shape, Point, Polygon, LineString
from folium import plugins
from folium.plugins import MarkerCluster, HeatMap

print(pd.__version__)
print(gpd.__version__)
print(folium.__version__)

1.3.3
0.10.1
0.12.1


    2. 프로젝트(1) 서울시 쏘카존 데이터를 활용한 시각화
       1) data load : socar zone data
       2) 시각화
          - base nap : 서울시 중심부 위도, 경도
          - MarkerCluster 객체 
          - map draw

In [2]:
#2. 프로젝트(1)  ... data load
path = os.getenv('HOME') + '/aiffel/socar_gis/data/20210823_socar_zone.csv'

socar_zone_info_df = pd.read_csv(path)
socar_zone_info_df.head()

zone_name         lng        lat region1  region2 region3
0    비전2 파출소사거리  127.102939  36.995989     경기도      평택시     비전동
1    수원시청역 9번출구  127.032953  37.262378     경기도  수원시　팔달구     인계동
2  목포 상동현대아파트 앞  126.415655  34.811289    전라남도      목포시      상동
3   단국대 산학협력관 앞  127.166626  36.832965    충청남도  천안시　동남구     신부동
4       목원대학교 앞  127.337858  36.329906   대전광역시       서구     도안동

In [3]:
#2. 프로젝트(1)  # base nap : 서울시 중심부 위도, 경도
center = [37.541, 126.986]

map = folium.Map(
    location=center,
    zoom_start=10,
    )
print('슝~')

슝~


In [4]:
#2. 프로젝트(1)  # MarkerCluster 객체 
marker_cluster = MarkerCluster().add_to(map)

#maker 객체 추가
for idx, row in socar_zone_info_df.iterrows():
    try:
        folium.Marker(
            location=[socar_zone_info_df.loc[idx, "lat"], socar_zone_info_df.loc[idx, "lng"]],
            popup=socar_zone_info_df.loc[idx, "zone_name"],
            icon=folium.Icon(color="cadetblue", icon="car", prefix="fa")            
        ).add_to(marker_cluster)
    except:
        pass

print('슝~')

슝~


In [5]:
#2. 프로젝트(1)  # map draw
map

    3. 프로젝트(2) 서울시 카페와 버스 정류장 밀도 데이터를 이용한 시각화
           1) 카페data 정리
              - data load
              - 카페data 전처리 : 업종data분류
              - 카페 위치데이터 리스트 만들기
           2) 버스data 정리
              - data load
              - 버스data 전처리 .. 컬럼명 변경
              - 버스 정류장 위치데이터 리스트 만들기
           3) 시각화 
              - Folium 초기 Map 객체 생성
              - 레이어 적용을 위한 그룹 만들기
              - 카페 밀도
              - 버스정류장 밀도
           4) 생성한 map 확인

In [6]:
#3. 프로젝트(2) ... 2) 버스data load
path = os.getenv('HOME') + '/aiffel/socar_gis/data/seoul_bus_line_info.csv'
bus_line_info_df =  pd.read_csv(path)
bus_line_info_df.head()

노선ID   노선명  순번       구간ID      정류소ID  ARS-ID        정류소명         X좌표  \
0  100100124  0017   1          0  102000271    3689     청암자이아파트  126.946517   
1  100100124  0017   2  102700549  102000204    3298  청암동강변삼성아파트  126.949304   
2  100100124  0017   3  102700550  102000227    3321       청심경로당  126.950449   
3  100100124  0017   4  102700551  102000210    3304    원효2동주민센터  126.950904   
4  100100124  0017   5  102700552  102000212    3306         산천동  126.953984   

         Y좌표  
0  37.534363  
1  37.533961  
2  37.533744  
3  37.534278  
4  37.535420

In [7]:
#3. 프로젝트(2) ... 2) 버스data 전처리 .. 컬럼명 변경
bus_line_info_df.rename(
    columns={
        "Y좌표": "lat",
        "X좌표": "lng",
    },
    inplace=True
)

bus_line_info_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 39363 entries, 0 to 39362
Data columns (total 9 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   노선ID    39363 non-null  int64  
 1   노선명     39363 non-null  object 
 2   순번      39363 non-null  int64  
 3   구간ID    39363 non-null  int64  
 4   정류소ID   39363 non-null  int64  
 5   ARS-ID  39363 non-null  int64  
 6   정류소명    39363 non-null  object 
 7   lng     39363 non-null  float64
 8   lat     39363 non-null  float64
dtypes: float64(2), int64(5), object(2)
memory usage: 2.7+ MB


In [8]:
#3. 프로젝트(2) ... 2) 버스 정류장 위치데이터 리스트 만들기
bus_station_location_data = [[row["lat"], row["lng"]] for _, row in bus_line_info_df.iterrows()]
print('슝~')
#bus_station_location_data

슝~


In [9]:
#3. 프로젝트(2) ... 3)시각화  ... # Folium 초기 Map 객체 생성 

center = [37.541, 126.986]

map = folium.Map(
    location=center,
    tiles= "Stamen Terrain", 
    zoom_start= 15
)
print('슝~')

슝~


In [14]:
#3. 프로젝트(2) ... 3) 시각화 # 레이어 적용을 위한 그룹 만들기
# 대표 그룹 만들기
fg = folium.FeatureGroup(name="groups")
map.add_child(fg)

# # 카페 그룹 만들기
# cafe = plugins.FeatureGroupSubGroup(fg, "cafe_density")
# map.add_child(cafe)

# 버스정류장 그룹 만들기
bus = plugins.FeatureGroupSubGroup(fg, "bus_group")
map.add_child(bus)

# 레이어 콘트롤 박스 만들기
folium.LayerControl(collapsed=False).add_to(map)

In [15]:
# #3. 프로젝트(2) ... 3) 시각화 .. # 카페 밀도
# plugins.HeatMap(seoul_cafe_location_data).add_to(cafe)

In [16]:
#3. 프로젝트(2) ... 3) 시각화 ... # 버스정류장 밀도
plugins.HeatMap(bus_station_location_data).add_to(bus)

In [17]:
#3. 프로젝트(2) ... 3) 시각화 ... # 생성한 맵 확인
map